<center><img src="https://github.com/pandas-dev/pandas/raw/main/web/pandas/static/img/pandas.svg" alt="pandas Logo" style="width: 800px;"/></center>

# Pandas Notebook 7: Merging DataFrames

This notebook will combine into one dataframe observations from two separate data sources: the NYS Mesonet, and ASOS sites located in New York. 

## Overview

1. Examine the NYSM and ASOS-derived datafiles for a particular day.
1. Remove (*drop*) unwanted columns from a DataFrame.
1. Use a dictionary to rename columns.
1. Merge columns from one DataFrame into another and re-index.
1. Add columns to a DataFrame
1. Concatenate one DataFrame into another.
1. Analyze the merged DataFrame.

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Pandas notebooks 1-7 | Necessary | Intro to `dict` |

* **Time to learn**: 30 minutes

---

## Imports

In [ ]:
import pandas as pd
import numpy as np

#### Examine the NYSM and ASOS-derived datafiles for a particular day

Read in NYSM 5-minute data from 8/4/2020 (during the passage of Hurricane Isaias through the region) and also read in the NYSM site table so we can extract latitude, longitude, and elevation. Also read in a table that has hourly METAR observations from ASOS sites in New York State. 

In [ ]:
nysm_data_file = '/spare11/atm533/data/nysm_data_20200804.csv'
nysm_sites_file = '/spare11/atm533/data/nysm_sites.csv'
nyasos_data_file = '/spare11/atm533/data/nyasos_data_20200804.txt'

In [ ]:
nysm_data = pd.read_csv(nysm_data_file)

In [ ]:
nysm_sites = pd.read_csv(nysm_sites_file)

Examine the ASOS data. Note the following differences in this dataset's format as compared to how the NYSM data is structured:
1. Its columns are named differently from those of the NYSM
1. Its columns are separated using whitespace, not tabs
1. Missing values are denoted by -9999.0, not null strings
1. The date/time is formatted differently.

In [ ]:
! head $nyasos_data_file

In [ ]:
nyasos_data = pd.read_csv(nyasos_data_file,delim_whitespace=True,na_values=[-9999.0])

Look at the first couple of rows in all three DataFrames.

In [ ]:
nysm_data.head(2)

In [ ]:
nysm_sites.head(2)

In [ ]:
nyasos_data.head(2)

#### Remove (*drop*) unwanted columns from a DataFrame

Our merged data file will contain only a subset of the columns from each data source. First, let's remove the unwanted columns from the NYSM file.

Use `inplace` so the Dataframe object is updated, and specify that we're referring to columns, not the default axis, which is row indices.

In [ ]:
nysm_data.drop(['temp_9m [degC]','precip_incremental [mm]','precip_local [mm]','precip_max_intensity [mm/min]',
       'avg_wind_speed_prop [m/s]', 'max_wind_speed_prop [m/s]','wind_speed_stddev_prop [m/s]', 'wind_direction_prop [degrees]',
       'wind_direction_stddev_prop [degrees]','wind_speed_stddev_sonic [m/s]','wind_direction_stddev_sonic [degrees]', 'solar_insolation [W/m^2]','snow_depth [cm]', 'frozen_soil_05cm [bit]',
       'frozen_soil_25cm [bit]', 'frozen_soil_50cm [bit]',
       'soil_temp_05cm [degC]', 'soil_temp_25cm [degC]',
       'soil_temp_50cm [degC]', 'soil_moisture_05cm [m^3/m^3]',
       'soil_moisture_25cm [m^3/m^3]', 'soil_moisture_50cm [m^3/m^3]'],inplace=True,axis='columns')

Examine what columns remain post-drop.

In [ ]:
nysm_data.columns

Now, drop any unwanted columns from the ASOS data file.

In [ ]:
nyasos_data.drop(['P01M'],axis='columns',inplace=True)

Examine the columns remaining in the ASOS data file

In [ ]:
nyasos_data.columns

Examine the columns in the NYSM Sites file

In [ ]:
nysm_sites.columns

#### Use a dictionary to rename columns

Each dataframe has varying column names. Let's standardize by creating a `dictionary` that will map current column names to common (and in some cases, much shorter) names.

In [ ]:
column_mapping = {'station' : 'STID',
                  'time': 'TIME',
                  'temp_2m [degC]': 'TMPC',
                  'relative_humidity [percent]': 'RELH',
                  'precip_incremental [mm]': 'PRCP',
                  'precip_local [mm]': 'PTOT',
                  'avg_wind_speed_sonic [m/s]': 'SPED',
                  'max_wind_speed_sonic [m/s]': 'GUMS',
                  'wind_direction_sonic [degrees]': 'DRCT', 
                  'station_pressure [mbar]': 'PRES',
                  'stid': 'STID',
                  'name': 'NAME',
                  'lat': 'SLAT',
                  'lon': 'SLON',
                  'elevation': 'SELV',
                  'STN':  'STID',
                  'YYMMDD/HHMM': 'TIME'}

For each of the three Dataframes, rename the columns according to our dictionary. Then examine each Dataframe to see how they look.

In [ ]:
nysm_data.rename(columns=column_mapping, inplace=True)

In [ ]:
nysm_data.head()

In [ ]:
nysm_sites.rename(columns=column_mapping, inplace=True)

In [ ]:
nysm_sites.head()

In [ ]:
nyasos_data.rename(columns=column_mapping, inplace=True)

In [ ]:
nyasos_data.head()

#### Merge columns from one DataFrame into another, and then re-index.</span>

Use `merge` to add the latitude, longitude, and elevation from the NYSM Sites dataframe to the NYSM Data one.
To do this, we take a subset of the nysm_sites dataframe containing the ones we want to merge, plus the station id column, since `merge` requires a common column for both dataframes. Note also that `merge` does not have an `inplace` option so we just redefine the `nysm_data` object.

In [ ]:
nysm_data = pd.merge(nysm_data,nysm_sites[['STID','SLAT','SLON','SELV']])

In [ ]:
nysm_data.head()

#### Make the NYSM and ASOS dataframes *multi-indexed* according to *site* and *time*. Convert the date/time from string to Datetime objects. 

First set the indexes

In [ ]:
nysm_data.set_index(['STID', 'TIME'], inplace = True)

In [ ]:
nysm_data.head()

The NYSM date/time strings can be automatically parsed into Datetime objects, recognized as in the UTC time zone.

In [ ]:
nysm_data.index.set_levels([nysm_data.index.levels[0], pd.to_datetime(nysm_data.index.levels[1])],inplace=True)

In [ ]:
nysm_data.head()

The ASOS data set needs to have its station id and date/times sorted in order for the multi-indexing to work properly.

In [ ]:
nyasos_data.sort_values(['STID','TIME'],inplace=True)

In [ ]:
nyasos_data.set_index(['STID', 'TIME'], inplace = True)

### Convert the date/time strings. Here, we need to specify how the string is formatted.

In [ ]:
nyasos_data.index.set_levels([nyasos_data.index.levels[0], pd.to_datetime(nyasos_data.index.levels[1],format="%y%m%d/%H%M",utc=True)],inplace=True)

In [ ]:
nyasos_data

#### Add columns to a DataFrame

The NYSM data does not contain dewpoint nor sea-level pressure yet. Calculate and create columns for dewpoint and sea-level pressure.

In [ ]:
tmpc = nysm_data['TMPC']
rh = nysm_data['RELH']
pres = nysm_data['PRES']
elev = nysm_data['SELV']

In [ ]:
sensorHeight = .5
# Reduce station pressure to SLP. Source: https://www.sandhurstweather.org.uk/barometric.pdf 
nysm_data['PMSL'] = pres/np.exp(-1*(elev+sensorHeight)/((tmpc+273.15) * 29.263))

In [ ]:
nysm_data['DWPC'] = 243.04*(np.log(rh/100)+((17.625*tmpc)/(243.04+tmpc)))/(17.625-np.log(rh/100)-((17.625*tmpc)/(243.04+tmpc)))

Now that we have calculated sea-level pressure, let's drop station pressure from the NYSM DataFrame since it does not appear in the ASOS one.

In [ ]:
nysm_data.drop('PRES',inplace=True,axis='columns')

In [ ]:
nysm_data

### Concatenate one DataFrame into another

Now, the two dataframes can be merged. We'll use the `concat` method to "glue" the rows from the ASOS table on to the NYSM one.

In [ ]:
nymerge_data = pd.concat([nysm_data,nyasos_data])

In [ ]:
nymerge_data

Let's rearrange the columns into a more logical order.

In [ ]:
colOrder = ['SLAT','SLON','SELV','TMPC','DWPC','RELH','PMSL','DRCT','SPED','GUMS']

In [ ]:
nymerge_data = nymerge_data.reindex(columns=colOrder)

<div class="alert alert-block alert-warning">
<b>Note:</b> Whenever you combine DataFrames, it's a very good idea to re-sort the indices. Although the new DataFrame may "look" correct, its indices may not be in what Pandas calls <b>lexical order</b>. We'll use Pandas <code>sort_index</code> for this purpose.</div>

In [ ]:
nymerge_data.sort_index(ascending=True, inplace=True)

In [ ]:
nymerge_data

### Analyze the merged DataFrame

Now, we have what we wanted ... one Dataframe that contains the same variables for both datasets. We can make selections on the multi-index Dataframe as we've done previously.

Get some general information about the `DataFrame`:

In [ ]:
nymerge_data.info()

Select one station

In [ ]:
nymerge_data.loc['ROC']

Select multiple stations and multiple times.

In [ ]:
nymerge_data.loc[(('ALB','VOOR'),('2020-08-04 17:45:00 UTC','2020-08-04 18:00:00 UTC')),('TMPC','DWPC')]

Use the *cross-section* method to select one index value and then display all values of the other index for selected columns.

In [ ]:
nymerge_data.xs('2020-08-04 18:00:00 UTC',level='TIME')[['TMPC','DWPC','RELH']]

<div class="alert alert-block alert-info">
    <b>Tip:</b> We could, of course, take this merged <code>DataFrame</code> and create a station plot with it ... which would show not only the NYSM data, but also the traditional ASOS network of stations!</div>

---
## Summary
* Pandas can efficiently combine datasets with different attributes into a single `DataFrame`.
* Pay attention to the row indexing in the resulting merged `DataFrame`.

### What's Next?
In the next notebook, we will explore Pandas' `groupby` function.

## Resources and References
1. [MetPy Monday Episode 94](https://www.youtube.com/watch?v=ncpYohRYG3I&list=PLQut5OXpV-0ir4IdllSt1iEZKTwFBa7kO&index=85&t=4s)
1. [MetPy Monday Episode 97](https://www.youtube.com/watch?v=rj2ZEAIbg1k&list=PLQut5OXpV-0ir4IdllSt1iEZKTwFBa7kO&index=88&ab_channel=Unidata)
1. [MetPy Monday Episode 98](https://www.youtube.com/watch?v=slUGaLyLJX0&list=PLQut5OXpV-0ir4IdllSt1iEZKTwFBa7kO&index=89&ab_channel=Unidata)
1. [National Weather Service Automated Surface Observing Systems (ASOS)](https://www.weather.gov/asos/)